 #### Project goal: For every hour of every day of the week, provide clusters that Uber can use to distribute its drivers. These clusters aim to have at least 90% of riders within 7 minutes of a cluster center at any moment.

 # Notebook Setup

## Imports

In [1]:
# Imports

import pandas as pd
import numpy as np

import plotly.express as px
import plotly.graph_objects as go

from IPython.display import clear_output

from typing import Union, List, Tuple
from numpy.typing import NDArray


## Read data

In [2]:
import os

def import_data(compression='xz'):
    filepath_local = 'clean_data.csv.xz'
    data = pd.read_csv(filepath_local, compression=compression)
    return data

data = import_data()


## Quick data cleaning

In [3]:
data = data.drop('base', axis=1)
data['date'] = pd.to_datetime(data['date'])
data['hour'] = data['date'].dt.hour
data['day'] = data['date'].dt.weekday


In [6]:
data.head()

Unnamed: 0      lat      lon                date  hour  day  year  month  \
0           0  40.7690 -73.9549 2014-04-01 00:11:00     0    1  2014      4   
1           1  40.7267 -74.0345 2014-04-01 00:17:00     0    1  2014      4   
2           2  40.7316 -73.9873 2014-04-01 00:21:00     0    1  2014      4   
3           3  40.7588 -73.9776 2014-04-01 00:28:00     0    1  2014      4   
4           4  40.7594 -73.9722 2014-04-01 00:33:00     0    1  2014      4   

   dayday  
0       1  
1       1  
2       1  
3       1  
4       1

In [5]:
data['year'] = data['date'].dt.year
data['month'] = data['date'].dt.month
data['dayday'] = data['date'].dt.day

## EDA

In [168]:
data.shape


(18804797, 6)

In [169]:
data_sample = data.sample(int(len(data)*0.005)) # sample 0.5% of data
fig = px.scatter_mapbox(data_sample, lat='lat', lon='lon')
fig.update_layout(mapbox_style="open-street-map", width=600, height=300,
                  margin=dict(l=0, r=0, b=0, t=0))
fig.show()


In [170]:
data_day_hour = data.groupby(['day', 'hour']).count().sort_values(by=['day', 'hour']).reset_index(drop=True).drop(['Unnamed: 0', 'lat', 'lon'], axis=1)
data_day_hour['day'] = data_day_hour.index // 24

fig = px.line(
    x=data_day_hour.index,
    y=data_day_hour.iloc[:,0],
    color=data_day_hour['day']
    )
fig.update_layout(
    xaxis=dict(
        tickvals=list(range(0, 25, 6)),
    )
)

Unfortunately plotly separates each trace by colour, so our line isnt continuous, but we get a decent idea of the amount of rides by hour of day of the week. We especially note that difference in rider behaviour between weeekdays and weekends, and the gradual increase of rides over the week.

 # Clustering

 ## Setup

In [171]:
# Create function to filter our data by day and hour
def filter_data(data, day, hour):
    return data[(data['day'] == day) & (data['hour'] == hour)]

# Create function to prepare our data before clustering
def prep_data(data, day, hour, limit=None):
    X = filter_data(data, day, hour) # Filter by day and hour
    X = X[['lat', 'lon']] # Select only coordinates
    
    if limit is not None:
        if len(X) > limit:
            X = X.sample(limit)
    
    return X

# Create function to plot all our clusters
def plot_clusters(data, labels):
    if type(data) != 'pandas.core.frame.DataFrame':
        data = pd.DataFrame(data)

    fig = go.Figure()

    for i in np.unique(labels):

        indices = np.where(labels == i)[0].tolist()
        lat = data.iloc[indices,0]
        lon = data.iloc[indices,1]

        fig.add_trace(go.Scattermapbox(lat=lat, lon=lon))

    fig.update_layout(mapbox_style="open-street-map",
                      margin=dict(l=0, r=0, t=20, b=0),
                      mapbox=dict(
                            zoom=8,
                            center=dict(lat=40.74, lon=-73.97)),
                      width=800,
                      height=300)
    return fig


 ## Different clustering algorithm tests

In [172]:
# Import cluster test metrics
from sklearn.metrics import silhouette_score, calinski_harabasz_score

# Prepare test data
cluster_test_data = prep_data(data, 0, 18).sample(10000, random_state=0)

# Prepare cluster test result dataframe
cluster_test_result = pd.DataFrame(columns=['algo',
                                            'cluster_amount',
                                            'calinski_harabasz_score',
                                            'silhouette_score',
                                            'standard_deviation',
                                            ])

 ### DBSCAN

In [173]:
from sklearn.cluster import DBSCAN

db = DBSCAN(eps=0.005, min_samples=10, metric='euclidean')
db.fit_predict(cluster_test_data)
print("{} clusters found.".format(
    np.max(np.unique(db.labels_))))

cluster_test_result.loc[len(cluster_test_result)] = ['dbscan',
                                                np.max(np.unique(db.labels_)),
                                                calinski_harabasz_score(cluster_test_data, db.labels_),
                                                silhouette_score(cluster_test_data, db.labels_),
                                                np.std(np.unique(db.labels_, return_counts=True)[1]),
                                                ]

plot_clusters(cluster_test_data, db.labels_)

40 clusters found.


DBSCAN struggles with the variable density of this problem. We have enormous clusters and many outliers.
It also has poor memory complexity (O(n^2)) due to its computation of a distance matrix, meaning we would have to create our clusters on only a sample of all our points.

Let's look at some other algorithms.

### HDBSCAN

In [174]:
from sklearn.cluster import HDBSCAN

hdb = HDBSCAN(min_cluster_size=10, min_samples=3, cluster_selection_epsilon=0.005)
hdb.fit_predict(cluster_test_data)
print("{} clusters found.".format(
    np.max(np.unique(hdb.labels_))))

cluster_test_result.loc[len(cluster_test_result)] = ['hdbscan',
                                                np.max(np.unique(hdb.labels_)),
                                                calinski_harabasz_score(cluster_test_data, hdb.labels_),
                                                silhouette_score(cluster_test_data, hdb.labels_),
                                                np.std(np.unique(hdb.labels_, return_counts=True)[1]),
                                                ]

plot_clusters(cluster_test_data, hdb.labels_)

46 clusters found.


HDBSCAN is a hierarchical version of DSCAN that with search over varying epsilon values to find the most stable solution. In theory, this makes it more robust and allows it to find clusters of varying density.

In practice, it struggles to create usable clusters due to their irregularity. It also is not immune to the memory issues we ran into with our original HDBSCAN algoirthm.

### K-Means

In [175]:
from sklearn.cluster import KMeans

kmeans = KMeans(n_clusters=25,
                random_state=0,
                n_init='auto')
kmeans.fit_predict(cluster_test_data)
print("{} clusters found.".format(
    np.max(np.unique(kmeans.labels_))))

cluster_test_result.loc[len(cluster_test_result)] = ['kmeans',
                                                np.max(np.unique(kmeans.labels_)),
                                                calinski_harabasz_score(cluster_test_data, kmeans.labels_),
                                                silhouette_score(cluster_test_data, kmeans.labels_),
                                                np.std(np.unique(kmeans.labels_, return_counts=True)[1]),
                                                ]

plot_clusters(cluster_test_data, kmeans.labels_)

24 clusters found.


K-Means, despite its simplicity, performs quite well. Our clusters are mostly regularly shaped but we do suffer from sizes that vary a lot. Let's also test Mini Batch K-Means to see if the performance speed up is meaningful:

In [176]:
from sklearn.cluster import MiniBatchKMeans

mb_kmeans = MiniBatchKMeans(n_clusters=25,
                random_state=0,
                n_init='auto')
mb_kmeans.fit_predict(cluster_test_data)
print("{} clusters found.".format(
    np.max(np.unique(mb_kmeans.labels_))))

cluster_test_result.loc[len(cluster_test_result)] = ['mb_kmeans',
                                                np.max(np.unique(mb_kmeans.labels_)),
                                                calinski_harabasz_score(cluster_test_data, mb_kmeans.labels_),
                                                silhouette_score(cluster_test_data, mb_kmeans.labels_),
                                                np.std(np.unique(mb_kmeans.labels_, return_counts=True)[1]),
                                                ]

plot_clusters(cluster_test_data, mb_kmeans.labels_)

c:\Users\rapha\anaconda3\envs\colab\lib\site-packages\sklearn\cluster\_kmeans.py:1972: UserWarning:

MiniBatchKMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can prevent it by setting batch_size >= 4096 or by setting the environment variable OMP_NUM_THREADS=4



24 clusters found.


Mini Batch K-Means seems to be about 10-20% faster (and sometimes actually slower) than the regular implementation, which is unlikely to be worth the performance tradeoff.

 ### BIRCH

In [177]:
model_threshold = 0.0005
model_branching_factor = 30

In [178]:
from sklearn.cluster import Birch

brc = Birch(threshold=model_threshold, branching_factor=model_branching_factor, n_clusters=25)
brc.fit_predict(cluster_test_data)
print("{} clusters found.".format(
    np.max(np.unique(brc.labels_)))
      )

cluster_test_result.loc[len(cluster_test_result)] = ['birch',
                                                np.max(np.unique(brc.labels_)),
                                                calinski_harabasz_score(cluster_test_data, brc.labels_),
                                                silhouette_score(cluster_test_data, brc.labels_),
                                                np.std(np.unique(brc.labels_, return_counts=True)[1]),
                                                ]

plot_clusters(cluster_test_data, brc.labels_)


24 clusters found.


The BIRCH algorithm builds a tree containing subcluster leaves which are then grouped into global clusters. It is very memory-efficient, which is particularly useful in our situation where we have 15 million points to cluster.

The results it provides are the best so far at a first visual evaluation, with regularly shaped and sized clusters that do well in capturing the concentrations of points and respecting the geographic boundaries of our data. BIRCH shows more usable clustering across varying densities and the produced borders better respect the actual geography of New York, notably Manhattan's separation from the rest of the city, alongside better isolating neighbourhoods based on their differing densities.

In [179]:
cluster_test_result

algo  cluster_amount  calinski_harabasz_score  silhouette_score  \
0     dbscan              40               245.036437          0.140891   
1    hdbscan              46               288.698100          0.175606   
2     kmeans              24             13920.605077          0.458938   
3  mb_kmeans              24              1273.084662          0.482295   
4      birch              24             10914.981447          0.397798   

   standard_deviation  
0         1142.128773  
1         1081.112570  
2          382.714515  
3          287.573017  
4          707.247057

**NOTE:** *these algorithms supply different results at each run, so the analyses of these metrics may not always be exact despite them representing the most common results*

Our model metrics quite clearly point to DBSCAN and its variation being the worst performers, K-Means and its variation being the best, with BIRCH sitting in the middle (although closer to K-Means performance than DBSCAN). The standard deviation of the amount of points in our clusters tells the same story, with both KMeans models having an SD below 1000 on our test data of 25,000. This is all goes without mentioning the significantly higher cluster counts found by the DBSCAN algorithms, which should lead to improved metrics.

However, as stated earlier, BIRCH better respects the actual geography of New York which likely means the cluster distances are more representative of real world distances. It also forms more regularly sized clusters which may be more usable to UBER. For these reasons, we will be using BIRCH clustering for our final clustering algorithm.

 ## BIRCH clustering across hours and days

 We are giving ourselves the goal of ensuring that:

 *90% of riders (based on our past data) will be within 7 minutes (~3 kilometers) of the center of their cluster*

Alongside providing the relative amount of riders in each cluster, this information will allow UBER to route their drivers dynamically into our clusters to ensure their customers are always nearby.

 To do this, we test BIRCH at different cluster amounts until we reach our 3km threshold value. We will search for cluster amounts where the 90th percentile distance to a cluster center is under 3km, which should roughly correspond with 7 minutes of driving. We will also be searching to minimize the cluster count to satisfy this condition, working under the assumption that having a lower cluster count means more exploitable insights for Uber.

First, we create a function that will find the specified percentile highest distance to a center.

In [180]:
# Create function to find specified percentile distance of our points to our cluster center
def cluster_distance(
    data: pd.DataFrame,
    d_labels: Union[List[int], NDArray[np.int_]],
    centers: Union[List[Tuple[float, float]], NDArray[np.float64]],
    c_labels: Union[List[int], NDArray[np.int_]],
    dx_col: str = 'lat',
    dy_col: str = 'lon',
    cx_col: str = 'center_x',
    cy_col: str = 'center_y',
    percentile: int = 90,
) -> float:
    
    '''
    Find a percentile distance between points and their cluster center
    
    Args:
        data (array|dataframe): points to measure distance between
        d_labels (array): labels to be assigned to data
        centers (array): center coordinates of each label
        c_labels (array): labels for centers
        dx_col (string): X column name for data points. Defaults to 'lat'
        dy_col (string): Y column name for data points. Defaults to 'lon'
        cx_col (string): X column name for centers. Defaults to 'center_x'
        cy_col (string): Y column name for centers. Defaults to 'center_y'
        max_length (int) : max length of array to treat. Defaults to 1_000_000
        percentile (int) : percentile of distances to find. Defaults to 90

    Returns:
        float: Specified1 percentile distance of distances between all pairs of points in data
    '''
    
    def merge_data(
            data: pd.DataFrame,
            d_labels: Union[List[int], NDArray[np.int_]],
            centers: Union[List[Tuple[float, float]], NDArray[np.float64]],
            c_labels: Union[List[int], NDArray[np.int_]]
        ) -> pd.DataFrame:
        
        centers = pd.DataFrame({
            'label' : c_labels,
            'center_x' : centers[:,0],
            'center_y' : centers[:,1],
        })
        
        data = data.copy()
        data['label'] = d_labels
        
        data = data.merge(centers, on='label')
        
        return data
    
    def calculate_distance(
        data : pd.DataFrame,
        dx_col : str,
        dy_col : str,
        cx_col : str,
        cy_col : str
        ) -> pd.Series:
        
        '''
        Find distances between a cluster's points and its center
        
        Args:
            data (pd.DataFrame): points of a cluster and their centers
            dx_col (str): X point column name
            dy_col (str): Y point column name
            cx_col (str): X center column name
            cy_col (str): Y center column name
            
        Returns:
            pd.Series: Distances of points to cluster center
        '''
        
        return np.sqrt((data[dx_col] - data[cx_col])**2 + (data[dy_col] - data[cy_col])**2)
    
    def coord_to_distance(degree_distance, K=110.574):
        return K * degree_distance
    
    
    data = merge_data(data, d_labels, centers, c_labels)
    
    return coord_to_distance(
        np.percentile(
            calculate_distance(data, dx_col, dy_col, cx_col, cy_col), percentile
        ))


Then, we create a function that performs a binary search through our cluster amounts and their percentile distances until we find a cluster amount that fits into our specified margin. For each of these sets of clusters, we take note of how they distribute our points and where their centers are. Since our BIRCH algorithm is not actually centroid based, we need to find another way to define our clusters: the calculation of a convex hull that defines each region.

In [181]:
from scipy.spatial import ConvexHull

def search_optimal_clusters(
    data : pd.DataFrame,
    max_distance,
    day : int,
    hour : int,
    threshold : float = 0.1,
    max_clusters : int = 128,
) -> int:
    
    max_dist_thresh = max_distance * threshold
    
    max_distance = [
        max_distance-max_dist_thresh,
        max_distance
        ]
    
    low = 1
    high = max_clusters
    
    while low <= high:
        
        mid = int((low+high)/2)
        model = Birch(threshold=model_threshold,
                      branching_factor=model_branching_factor,
                      n_clusters=mid).fit(data)
        distance = cluster_distance(data, model.labels_, model.subcluster_centers_, model.subcluster_labels_)
        
        # If we meet our criteria then
        if (distance > max_distance[0]) & (distance < max_distance[1]):
            
            # Main+cluster dataframe
            df_1 = pd.DataFrame({
                'cluster_count' : len(np.unique(model.labels_)),
                'day' : day,
                'hour' : hour,
                'label' : np.unique(model.labels_, return_counts=True)[0],
                'points' : np.unique(model.labels_, return_counts=True)[1],
                'points_per' : np.unique(model.labels_, return_counts=True)[1] / len(data)
                })
            
            # Cluster center dataframe
            df_2 = pd.DataFrame({
                'label' : model.subcluster_labels_,
                'center_x' : model.subcluster_centers_[:,0],
                'center_y' : model.subcluster_centers_[:,1]
            })
            
            # Convex hull dataframe
            df_3 = data.copy()
            df_3['label'] =  model.labels_
            df_3 = df_3.drop_duplicates()
            hull_vertices, hull_surfaces = [], []
            
            # Compute hull for every cluster
            for label in range(len(np.unique(model.labels_))):
                hull_data = df_3[df_3['label'] == label].reset_index().drop(['label', 'index'], axis=1)
            
                # Check we have 3 or more points before computing the region
                if len(df_3[df_3['label'] == label]) >= 3:
                    hull = ConvexHull(hull_data)
                    hull_index = hull.vertices
                    hull_surface = hull.volume
                else:
                    hull_index = None
                    hull_surface = None
                
                # If previous check was none then we can't append the data and need to pass None instead
                if hull_index is not None:
                    # NOTE: need to turn this into np array instead of dataframe
                    hull_vertex = hull_data.loc[hull_index].to_numpy()
                    hull_vertices.append(hull_vertex)
                else:
                    hull_vertices.append(None)
                hull_surfaces.append(hull_surface)

            # Get mean coords for each label
            df_2 = df_2.groupby('label').mean()
            
            # Add new columns
            df_2['region_surface'] = hull_surfaces
            df_2['region_vertices'] = hull_vertices
            
            # Create final dataframe to return
            df_result = df_1.merge(df_2, on='label')
            return df_result
        
        # Continue binary search if condition is not met
        elif distance > max_distance[1]:
            low = mid + 1
        elif distance < max_distance[0]:
            high = mid - 1

 Now that we have a function that allows us to find an amount of clusters that satisfies a given distance condition, we can run this on every hour of every day of the week

In [183]:
import time

final_clusters = pd.DataFrame(columns=['day', 'hour', 'label', 'points', 'points_per', 'center_x',
       'center_y'])

last_durations = []

# iterate over every day of the week
for day in range(7):
    # iterate over every hour of every day
    for hour in range(24):
        start_time = time.time()
        print("Now searching day {} and hour {}".format(day+1,hour))
        
        search_data = prep_data(data, day, hour, limit=50_000)
        search_result = search_optimal_clusters(search_data, 3, day, hour)
        final_clusters = pd.concat([final_clusters, search_result])
        
        # Find time remaining by looking at average time of past iterations
        clear_output()
        end_time = time.time()
        duration = end_time - start_time
        last_durations.append(duration)
        time_remaining = (7*24 - day*24 - hour - 1) * np.mean(last_durations)
        print(f"Last search took: {round(duration, 1)} seconds")
        print(f"Estimated time remaining: {round(time_remaining)} seconds or {round(time_remaining/60, 1)} minutes")


Last search took: 10.9 seconds
Estimated time remaining: 0 seconds or 0.0 minutes


Binary searching to find 168 (24 hours a day, 7 days a week) optimal clustering solutions takes just under 3 hours (162 minutes), which I believe is an acceptable time investment given the fact that this solution only needs to calculated once.

For the sake of this project, I have limited the amount of data fed into this so that it runs much faster (maximum of 50,000 points, instead of up to 200,000). This shortens our search to around 45 minutes.

In [186]:
# Save our results locally
final_clusters.to_csv(r'C:\Users\rapha\My Drive\Work\jedha_dsfs\coursework\p_uber\final_clusters.csv')

In [184]:
# Take a look at our output
final_clusters.sample(5)

day hour label points  points_per   center_x   center_y  cluster_count  \
34   2    1    34   1754     0.05446  40.709344 -74.009870           40.0   
10   5   13    10     19     0.00038  40.734208 -73.605189           48.0   
20   3   13    20     11     0.00022  40.754482 -74.267236           40.0   
26   5   14    26    122     0.00244  40.736429 -74.039611           48.0   
16   6   21    16     49     0.00098  40.652326 -73.722567           40.0   

    region_surface                                    region_vertices  
34        0.000196  [[40.7182, -74.015], [40.7159, -74.0086], [40....  
10        0.008823  [[40.6683, -73.5541], [40.6575, -73.645], [40....  
20        0.009916  [[40.8155, -74.3107], [40.8902, -74.2504], [40...  
26        0.002475  [[40.6994, -74.0537], [40.7061, -74.0994], [40...  
16        0.006987  [[40.699, -73.7196], [40.5841, -73.6399], [40....

Now that we have our final results to supply to UBER, we can have some fun previewing (kind of) our optimal solutions. I say "kind of" because we will be previewing the results of a BIRCH clustering with the same parameters, but that does not necessary guarantee the same results as our initial clusters. That's why we need to supply the cluster regions themselves rather than just the centroids.

In [185]:
def plot_optimal_cluster(data, day, hour):
    # Filter data to specified day and hour
    data = data.copy()
    data = filter_data(data, day, hour)
    
    # Create figure and plot x,y points of every cluster in our data recursively (unless the region is None)
    fig = go.Figure()
    for cluster in range(len(data)):
        if data['region_vertices'][cluster] is not None:
            fig.add_trace(go.Scattermapbox(
                lat=np.array(data['region_vertices'][cluster])[:,0],
                lon=np.array(data['region_vertices'][cluster])[:,1],
                mode='lines',
                fill='toself',
            ))
        else:
            continue

    # Update layout specifying mapbox style and other visual parameters
    fig.update_layout(mapbox_style="open-street-map",
                      margin=dict(l=0, r=0, t=20, b=0),
                      mapbox=dict(
                            zoom=8,
                            center=dict(lat=40.74, lon=-73.97)),
                      width=600,
                      height=300)
    
    fig.show()

# Ask user to specify day and hour
u_day, u_hour = int(input("What day would you like to see clusters for?")), int(input("What hour would you like to see clusters for?"))

plot_optimal_cluster(final_clusters, u_day, u_hour)

Here is day 1, hour 18 for example (rush hour on tuesday).

In [196]:
print(
    f"To satisfy our conditions, our algorithm found {filter_data(final_clusters, u_day, u_hour)['cluster_count'][0]} clusters on day {u_day} and hour {u_hour}.",
    '\n',
    'Here is the percentage of points assigned to each cluster (which gives UBER an idea of how to distribute their drivers):',
    '\n'*2,
    filter_data(final_clusters, u_day, u_hour)[['points_per']].sort_values(by='points_per', ascending=False).head()*100,
    '\n'*2,
    filter_data(final_clusters, u_day, u_hour)[['points_per']].sort_values(by='points_per', ascending=False).tail()*100
    )

To satisfy our conditions, our algorithm found 31.0 clusters on day 1 and hour 18. 
 Here is the percentage of points assigned to each cluster (which gives UBER an idea of how to distribute their drivers): 

     points_per
6       25.150
0       24.460
30      16.518
25      10.584
1        4.108 

     points_per
18       0.008
26       0.004
24       0.002
23       0.002
19       0.002
